In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = None
pd.options.display.max_rows = None
pd.options.display.float_format = '{:.6f}'.format
from sklearn.metrics import confusion_matrix,accuracy_score, f1_score, classification_report
from sklearn.metrics import roc_curve, roc_auc_score
from sklearn.model_selection import train_test_split

In [2]:
from sklearn.ensemble import AdaBoostClassifier, GradientBoostingClassifier
from xgboost import XGBClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB, BernoulliNB, MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.pipeline import Pipeline
from sklearn.metrics import confusion_matrix,accuracy_score, f1_score, classification_report, precision_score, recall_score
from sklearn.model_selection import RandomizedSearchCV,StratifiedKFold
from catboost import CatBoostClassifier
from lightgbm import LGBMClassifier
from scipy.stats import randint as sp_randint
from scipy.stats import uniform as sp_uniform

In [3]:
df_new = pd.read_csv('no-show_new.csv')

In [4]:
from sklearn.preprocessing import StandardScaler

df_num = df_new[['Age','Waitingperiod']]
df_cat = df_new.drop(['Age','Waitingperiod'],axis = 1)

ss = StandardScaler()

num_ss = ss.fit_transform(df_num)

df_num_ss = pd.DataFrame(num_ss, columns = df_num.columns)

df_new2 = pd.concat([df_num_ss, df_cat], axis = 1)

df_new2.head()

Age  Waitingperiod  Gender  Scholarship  Hipertension  Diabetes  \
0  0.763792      -0.614978       0     0.000000             1         0   
1  0.763792      -0.614978       1     0.000000             0         0   
2  1.027524      -0.614978       0     0.000000             0         0   
3 -1.346059      -0.614978       0     0.000000             0         0   
4  0.763792      -0.614978       0     0.000000             1         1   

   Alcoholism  Handcap  SMS_received  No-show  prior_appointments  \
0    0.000000 0.000000      0.000000        0            0.000000   
1    0.000000 0.000000      0.000000        0            1.000000   
2    0.000000 0.000000      0.000000        0            0.000000   
3    0.000000 0.000000      0.000000        0            1.000000   
4    0.000000 0.000000      0.000000        0            0.000000   

   regular_patient  prior_no_shows  Neighbourhood_Group1  \
0                0        0.000000                     0   
1                1        0.000000                     0   
2                0        0.000000                     1   
3                1        0.000000                     1   
4                0        0.000000                     0   

   Neighbourhood_Group2  Neighbourhood_Group3  Neighbourhood_Group4  \
0                     0                     1                     0   
1                     0                     1                     0   
2                     0                     0                     0   
3                     0                     0                     0   
4                     0                     1                     0   

   Neighbourhood_Group5  Neighbourhood_Group6  Neighbourhood_Group7  
0                     0                     0                     0  
1                     0                     0                     0  
2                     0                     0                     0  
3                     0                     0                     0  
4                     0                     0                     0

In [5]:
X = df_new2.drop('No-show', axis = 1)
y = df_new2['No-show']

X_train, X_test, y_train, y_test = train_test_split(X, y, random_state = 10, test_size = 0.3, stratify=y) 

In [6]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression())
])

In [7]:
params_dt = {'max_features':sp_randint(1,15),
          'max_depth': sp_randint(2,10),
         'min_samples_leaf': sp_randint(10,50),
         'criterion':['gini','entropy']}

rsearch_dt = RandomizedSearchCV(estimator = DecisionTreeClassifier(random_state = 42), param_distributions = params_dt, n_iter = 100, cv = 5, scoring = 'roc_auc', random_state = 42)

rsearch_dt.fit(X_train, y_train)

RandomizedSearchCV(cv=5, estimator=DecisionTreeClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'criterion': ['gini', 'entropy'],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000261989F04F0>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000261989EC8B0>,
                                        'min_samples_leaf': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000261989ECEE0>},
                   random_state=42, scoring='roc_auc')

In [8]:
rsearch_dt.best_params_

{'criterion': 'entropy',
 'max_depth': 7,
 'max_features': 11,
 'min_samples_leaf': 37}

In [9]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [10]:
params_rf = {'n_estimators':sp_randint(50,150),
          'max_features':sp_randint(1,15),
          'max_depth': sp_randint(2,10),
         'min_samples_leaf': sp_randint(10,50),
         'criterion':['gini','entropy']}

rsearch_rf = RandomizedSearchCV(estimator = RandomForestClassifier(random_state = 42), param_distributions = params_rf, n_iter = 100, cv = 5, scoring = 'roc_auc', random_state = 42)

rsearch_rf.fit(X_train, y_train)

RandomizedSearchCV(cv=5, estimator=RandomForestClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'criterion': ['gini', 'entropy'],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000261999DB4F0>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000261999C8310>,
                                        'min_samples_leaf': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000261999C8070>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000261999DBD90>},
                   random_state=42, scoring='roc_auc')

In [11]:
rsearch_rf.best_params_

{'criterion': 'entropy',
 'max_depth': 9,
 'max_features': 10,
 'min_samples_leaf': 11,
 'n_estimators': 50}

In [12]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [13]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [14]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [15]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [16]:
params_ada = {'n_estimators':sp_randint(20,150),
          'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

rsearch_ada = RandomizedSearchCV(estimator = AdaBoostClassifier(random_state = 42), param_distributions = params_ada, n_iter = 100, cv = 5, scoring = 'roc_auc', random_state = 42)

rsearch_ada.fit(X_train, y_train)

RandomizedSearchCV(cv=5, estimator=AdaBoostClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1, 2, 3, 4, 5],
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000026199A207C0>},
                   random_state=42, scoring='roc_auc')

In [17]:
rsearch_ada.best_params_

{'learning_rate': 1, 'n_estimators': 122}

In [18]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [19]:
params_gb = {'n_estimators':sp_randint(50,200),
          'max_features':sp_randint(1,15),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

rsearch_gb = RandomizedSearchCV(estimator = GradientBoostingClassifier(random_state = 42), param_distributions = params_gb, n_iter = 100, cv = 5, scoring = 'roc_auc', random_state = 42)

rsearch_gb.fit(X_train, y_train)

RandomizedSearchCV(cv=5, estimator=GradientBoostingClassifier(random_state=42),
                   n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1, 2, 3, 4, 5],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000026199A36F10>,
                                        'max_features': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000261989CFE50>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000026199A368E0>},
                   random_state=42, scoring='roc_auc')

In [20]:
rsearch_gb.best_params_

{'learning_rate': 0.1, 'max_depth': 6, 'max_features': 9, 'n_estimators': 52}

In [21]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [22]:
params_cb = {'n_estimators':sp_randint(50,200),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1]}

rsearch_cb = RandomizedSearchCV(estimator = CatBoostClassifier(random_state = 42), param_distributions = params_cb, n_iter = 100, cv = 5, scoring = 'roc_auc', random_state = 42)

rsearch_cb.fit(X_train, y_train)

0:	learn: 0.6885419	total: 150ms	remaining: 21.2s
1:	learn: 0.6840235	total: 154ms	remaining: 10.8s
2:	learn: 0.6795387	total: 157ms	remaining: 7.25s
3:	learn: 0.6751848	total: 159ms	remaining: 5.49s
4:	learn: 0.6708426	total: 162ms	remaining: 4.44s
5:	learn: 0.6666637	total: 165ms	remaining: 3.73s
6:	learn: 0.6625176	total: 167ms	remaining: 3.22s
7:	learn: 0.6584486	total: 170ms	remaining: 2.84s
8:	learn: 0.6544910	total: 187ms	remaining: 2.77s
9:	learn: 0.6506509	total: 190ms	remaining: 2.51s
10:	learn: 0.6468143	total: 193ms	remaining: 2.3s
11:	learn: 0.6430774	total: 196ms	remaining: 2.12s
12:	learn: 0.6394741	total: 199ms	remaining: 1.97s
13:	learn: 0.6358574	total: 202ms	remaining: 1.84s
14:	learn: 0.6322838	total: 205ms	remaining: 1.73s
15:	learn: 0.6287707	total: 207ms	remaining: 1.63s
16:	learn: 0.6253654	total: 210ms	remaining: 1.54s
17:	learn: 0.6219401	total: 213ms	remaining: 1.46s
18:	learn: 0.6186679	total: 215ms	remaining: 1.39s
19:	learn: 0.6155196	total: 218ms	remainin

58:	learn: 0.5242103	total: 181ms	remaining: 255ms
59:	learn: 0.5225201	total: 184ms	remaining: 251ms
60:	learn: 0.5208916	total: 187ms	remaining: 248ms
61:	learn: 0.5192595	total: 189ms	remaining: 244ms
62:	learn: 0.5176519	total: 192ms	remaining: 241ms
63:	learn: 0.5161374	total: 194ms	remaining: 237ms
64:	learn: 0.5145928	total: 197ms	remaining: 233ms
65:	learn: 0.5130612	total: 200ms	remaining: 230ms
66:	learn: 0.5115673	total: 202ms	remaining: 227ms
67:	learn: 0.5100605	total: 205ms	remaining: 223ms
68:	learn: 0.5085858	total: 208ms	remaining: 220ms
69:	learn: 0.5071173	total: 210ms	remaining: 216ms
70:	learn: 0.5057451	total: 213ms	remaining: 213ms
71:	learn: 0.5043687	total: 215ms	remaining: 209ms
72:	learn: 0.5029751	total: 218ms	remaining: 206ms
73:	learn: 0.5016555	total: 220ms	remaining: 202ms
74:	learn: 0.5003315	total: 223ms	remaining: 199ms
75:	learn: 0.4990863	total: 225ms	remaining: 196ms
76:	learn: 0.4977688	total: 228ms	remaining: 192ms
77:	learn: 0.4965196	total: 231

140:	learn: 0.4442689	total: 372ms	remaining: 2.64ms
141:	learn: 0.4437560	total: 375ms	remaining: 0us
0:	learn: 0.6885500	total: 3.31ms	remaining: 466ms
1:	learn: 0.6840302	total: 6.06ms	remaining: 424ms
2:	learn: 0.6795196	total: 10.9ms	remaining: 506ms
3:	learn: 0.6751487	total: 13.6ms	remaining: 470ms
4:	learn: 0.6708708	total: 16.3ms	remaining: 446ms
5:	learn: 0.6667611	total: 18.8ms	remaining: 426ms
6:	learn: 0.6625940	total: 21.3ms	remaining: 410ms
7:	learn: 0.6585514	total: 23.8ms	remaining: 398ms
8:	learn: 0.6545284	total: 26.4ms	remaining: 391ms
9:	learn: 0.6506901	total: 29ms	remaining: 383ms
10:	learn: 0.6468296	total: 31.6ms	remaining: 377ms
11:	learn: 0.6430781	total: 34.2ms	remaining: 370ms
12:	learn: 0.6394641	total: 36.8ms	remaining: 365ms
13:	learn: 0.6358265	total: 39.4ms	remaining: 360ms
14:	learn: 0.6322340	total: 42ms	remaining: 356ms
15:	learn: 0.6287005	total: 44.7ms	remaining: 352ms
16:	learn: 0.6252488	total: 47.4ms	remaining: 348ms
17:	learn: 0.6218036	total:

61:	learn: 0.5186996	total: 179ms	remaining: 231ms
62:	learn: 0.5170881	total: 182ms	remaining: 228ms
63:	learn: 0.5155651	total: 184ms	remaining: 224ms
64:	learn: 0.5140133	total: 187ms	remaining: 221ms
65:	learn: 0.5124680	total: 189ms	remaining: 218ms
66:	learn: 0.5109710	total: 192ms	remaining: 215ms
67:	learn: 0.5094581	total: 195ms	remaining: 212ms
68:	learn: 0.5079836	total: 197ms	remaining: 209ms
69:	learn: 0.5065100	total: 200ms	remaining: 206ms
70:	learn: 0.5051331	total: 202ms	remaining: 202ms
71:	learn: 0.5037506	total: 205ms	remaining: 199ms
72:	learn: 0.5023991	total: 207ms	remaining: 196ms
73:	learn: 0.5010782	total: 210ms	remaining: 193ms
74:	learn: 0.4997539	total: 213ms	remaining: 190ms
75:	learn: 0.4984544	total: 215ms	remaining: 187ms
76:	learn: 0.4971292	total: 217ms	remaining: 184ms
77:	learn: 0.4959011	total: 220ms	remaining: 181ms
78:	learn: 0.4946545	total: 223ms	remaining: 178ms
79:	learn: 0.4934368	total: 225ms	remaining: 175ms
80:	learn: 0.4922226	total: 228

79:	learn: 0.4955696	total: 200ms	remaining: 103ms
80:	learn: 0.4943798	total: 203ms	remaining: 100ms
81:	learn: 0.4932089	total: 205ms	remaining: 97.5ms
82:	learn: 0.4920671	total: 207ms	remaining: 94.9ms
83:	learn: 0.4909213	total: 209ms	remaining: 92.3ms
84:	learn: 0.4898404	total: 212ms	remaining: 89.7ms
85:	learn: 0.4887575	total: 214ms	remaining: 87.1ms
86:	learn: 0.4876881	total: 216ms	remaining: 84.5ms
87:	learn: 0.4865892	total: 218ms	remaining: 81.9ms
88:	learn: 0.4855964	total: 221ms	remaining: 79.3ms
89:	learn: 0.4845392	total: 223ms	remaining: 76.8ms
90:	learn: 0.4835229	total: 225ms	remaining: 74.2ms
91:	learn: 0.4825090	total: 227ms	remaining: 71.7ms
92:	learn: 0.4815379	total: 230ms	remaining: 69.2ms
93:	learn: 0.4805936	total: 232ms	remaining: 66.6ms
94:	learn: 0.4796189	total: 234ms	remaining: 64.1ms
95:	learn: 0.4786843	total: 236ms	remaining: 61.6ms
96:	learn: 0.4777456	total: 239ms	remaining: 59ms
97:	learn: 0.4768044	total: 241ms	remaining: 56.5ms
98:	learn: 0.475

...

75:	learn: 0.4003320	total: 583ms	remaining: 867ms
76:	learn: 0.4002933	total: 594ms	remaining: 864ms
77:	learn: 0.4002458	total: 598ms	remaining: 850ms
78:	learn: 0.4002009	total: 609ms	remaining: 847ms
79:	learn: 0.4000854	total: 625ms	remaining: 851ms
80:	learn: 0.4000404	total: 629ms	remaining: 838ms
81:	learn: 0.3999909	total: 633ms	remaining: 826ms
82:	learn: 0.3999300	total: 637ms	remaining: 813ms
83:	learn: 0.3998691	total: 641ms	remaining: 801ms
84:	learn: 0.3998287	total: 655ms	remaining: 801ms
85:	learn: 0.3997453	total: 659ms	remaining: 789ms
86:	learn: 0.3996613	total: 670ms	remaining: 785ms
87:	learn: 0.3996121	total: 685ms	remaining: 786ms
88:	learn: 0.3995819	total: 688ms	remaining: 773ms
89:	learn: 0.3994872	total: 699ms	remaining: 769ms
90:	learn: 0.3994408	total: 703ms	remaining: 757ms
91:	learn: 0.3994007	total: 706ms	remaining: 745ms
92:	learn: 0.3993346	total: 710ms	remaining: 733ms
93:	learn: 0.3992675	total: 731ms	remaining: 739ms
94:	learn: 0.3991449	total: 746

0:	learn: 0.6930974	total: 3.82ms	remaining: 218ms
1:	learn: 0.6930546	total: 7.33ms	remaining: 205ms
2:	learn: 0.6930053	total: 17.4ms	remaining: 319ms
3:	learn: 0.6929619	total: 34.4ms	remaining: 465ms
4:	learn: 0.6929151	total: 38ms	remaining: 402ms
5:	learn: 0.6928669	total: 41.2ms	remaining: 357ms
6:	learn: 0.6928216	total: 44.4ms	remaining: 324ms
7:	learn: 0.6927725	total: 47.8ms	remaining: 298ms
8:	learn: 0.6927290	total: 64.7ms	remaining: 352ms
9:	learn: 0.6926822	total: 67.5ms	remaining: 324ms
10:	learn: 0.6926335	total: 94.8ms	remaining: 405ms
11:	learn: 0.6925898	total: 98.1ms	remaining: 376ms
12:	learn: 0.6925402	total: 109ms	remaining: 378ms
13:	learn: 0.6924964	total: 126ms	remaining: 395ms
14:	learn: 0.6924516	total: 129ms	remaining: 370ms
15:	learn: 0.6924016	total: 140ms	remaining: 368ms
16:	learn: 0.6923577	total: 156ms	remaining: 375ms
17:	learn: 0.6923082	total: 159ms	remaining: 353ms
18:	learn: 0.6922629	total: 162ms	remaining: 333ms
19:	learn: 0.6922174	total: 165

55:	learn: 0.6905364	total: 625ms	remaining: 22.3ms
56:	learn: 0.6904897	total: 629ms	remaining: 11ms
57:	learn: 0.6904433	total: 657ms	remaining: 0us
0:	learn: 0.6930977	total: 18ms	remaining: 1.03s
1:	learn: 0.6930544	total: 21.3ms	remaining: 596ms
2:	learn: 0.6930051	total: 31.3ms	remaining: 575ms
3:	learn: 0.6929617	total: 47.2ms	remaining: 637ms
4:	learn: 0.6929098	total: 50.8ms	remaining: 538ms
5:	learn: 0.6928672	total: 54.2ms	remaining: 470ms
6:	learn: 0.6928206	total: 57.4ms	remaining: 418ms
7:	learn: 0.6927708	total: 77.7ms	remaining: 486ms
8:	learn: 0.6927277	total: 81ms	remaining: 441ms
9:	learn: 0.6926807	total: 107ms	remaining: 516ms
10:	learn: 0.6926317	total: 111ms	remaining: 474ms
11:	learn: 0.6925885	total: 123ms	remaining: 471ms
12:	learn: 0.6925406	total: 126ms	remaining: 437ms
13:	learn: 0.6924942	total: 130ms	remaining: 407ms
14:	learn: 0.6924499	total: 139ms	remaining: 398ms
15:	learn: 0.6923995	total: 154ms	remaining: 405ms
16:	learn: 0.6923551	total: 169ms	rema

105:	learn: 0.4008200	total: 590ms	remaining: 329ms
106:	learn: 0.4007705	total: 594ms	remaining: 322ms
107:	learn: 0.4007375	total: 598ms	remaining: 315ms
108:	learn: 0.4006669	total: 601ms	remaining: 309ms
109:	learn: 0.4006509	total: 605ms	remaining: 302ms
110:	learn: 0.4006340	total: 608ms	remaining: 296ms
111:	learn: 0.4005642	total: 612ms	remaining: 290ms
112:	learn: 0.4005186	total: 616ms	remaining: 283ms
113:	learn: 0.4004731	total: 619ms	remaining: 277ms
114:	learn: 0.4004264	total: 623ms	remaining: 271ms
115:	learn: 0.4004013	total: 627ms	remaining: 265ms
116:	learn: 0.4003799	total: 632ms	remaining: 259ms
117:	learn: 0.4003657	total: 635ms	remaining: 253ms
118:	learn: 0.4003436	total: 638ms	remaining: 247ms
119:	learn: 0.4002612	total: 642ms	remaining: 241ms
120:	learn: 0.4002199	total: 645ms	remaining: 235ms
121:	learn: 0.4001734	total: 649ms	remaining: 229ms
122:	learn: 0.4001158	total: 653ms	remaining: 223ms
123:	learn: 0.4000740	total: 656ms	remaining: 217ms
124:	learn: 

RandomizedSearchCV(cv=5,
                   estimator=<catboost.core.CatBoostClassifier object at 0x0000026199A221C0>,
                   n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000026199A38DF0>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000026199D91460>},
                   random_state=42, scoring='roc_auc')

In [23]:
rsearch_cb.best_params_

{'learning_rate': 0.1, 'max_depth': 6, 'n_estimators': 165}

In [24]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [25]:
params_lgbm = {'n_estimators':sp_randint(50,200),
          'num_leaves':sp_randint(2,50),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

rsearch_lgbm = RandomizedSearchCV(estimator = LGBMClassifier(random_state = 42), param_distributions = params_lgbm, n_iter = 100, cv = 5, scoring = 'roc_auc', random_state = 42)

rsearch_lgbm.fit(X_train, y_train)

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(random_state=42), n_iter=100,
                   param_distributions={'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1, 2, 3, 4, 5],
                                        'max_depth': <scipy.stats._distn_infrastructure.rv_frozen object at 0x000002619B3E7C70>,
                                        'n_estimators': <scipy.stats._distn_infrastructure.rv_frozen object at 0x000002619B3E79A0>,
                                        'num_leaves': <scipy.stats._distn_infrastructure.rv_frozen object at 0x0000026199A203A0>},
                   random_state=42, scoring='roc_auc')

In [26]:
rsearch_lgbm.best_params_

{'learning_rate': 0.1, 'max_depth': 6, 'n_estimators': 120, 'num_leaves': 23}

In [27]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [28]:
params_xgb = {'gamma':sp_randint(0,5),
          'max_depth': sp_randint(2,10),
         'learning_rate':[0.0001,0.001,0.01,0.1,1,2,3,4,5]}

rsearch_xgb = RandomizedSearchCV(estimator = XGBClassifier(random_state = 42), param_distributions = params_xgb, n_iter = 100, cv = 5, scoring = 'roc_auc', random_state = 42)

rsearch_xgb.fit(X_train, y_train)

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, gamma=None,
                                           gpu_id=None, grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate=None, max_bin=None,...
                                           num_parallel_tree=None,
                                           predictor=None, random_state

In [29]:
rsearch_xgb.best_params_

{'gamma': 4, 'learning_rate': 0.1, 'max_depth': 6}

In [30]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [31]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]

for pipe in pipe_all:
  pipe.fit(X_train, y_train)

0:	learn: 0.6491319	total: 4.12ms	remaining: 676ms
1:	learn: 0.6126479	total: 8.13ms	remaining: 663ms
2:	learn: 0.5820690	total: 12.2ms	remaining: 658ms
3:	learn: 0.5568437	total: 16.3ms	remaining: 655ms
4:	learn: 0.5352917	total: 24.4ms	remaining: 782ms
5:	learn: 0.5175254	total: 28.1ms	remaining: 746ms
6:	learn: 0.5021412	total: 31.6ms	remaining: 713ms
7:	learn: 0.4888308	total: 35.1ms	remaining: 689ms
8:	learn: 0.4780890	total: 53.7ms	remaining: 931ms
9:	learn: 0.4682793	total: 57.3ms	remaining: 888ms
10:	learn: 0.4596616	total: 60.9ms	remaining: 853ms
11:	learn: 0.4526916	total: 64.7ms	remaining: 825ms
12:	learn: 0.4461484	total: 83.6ms	remaining: 978ms
13:	learn: 0.4411896	total: 87.7ms	remaining: 946ms
14:	learn: 0.4364287	total: 99.3ms	remaining: 993ms
15:	learn: 0.4323837	total: 103ms	remaining: 958ms
16:	learn: 0.4293347	total: 107ms	remaining: 928ms
17:	learn: 0.4259297	total: 110ms	remaining: 900ms
18:	learn: 0.4230640	total: 130ms	remaining: 999ms
19:	learn: 0.4207473	total

In [32]:
model_scores = {"Model Name" : [],
    'Accuracy train': [], 'Precision train': [], 'Recall train': [], 'F1 train': [], 'ROC AUC train': [],
    'Accuracy test': [], 'Precision test': [], 'Recall test': [], 'F1 test': [], 'ROC AUC test': []} # , 'CV-5-Mean': [], 'CV-5-SD': []}

for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0])
    
    model_scores['Accuracy train'].append(model.score(X_train, y_train))
    pred_tr = model.predict(X_train)
    prob_tr = model.predict_proba(X_train)[:,1]
    model_scores['Precision train'].append(precision_score(y_train, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train, pred_tr))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    # model_scores['CV-5-Mean'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    # model_scores['CV-5-SD'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

In [33]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.818000   
1                              DecisionTreeClassifier        0.827900   
2                              RandomForestClassifier        0.833400   
3                                          GaussianNB        0.792700   
4                                         BernoulliNB        0.819400   
5                                  AdaBoostClassifier        0.829500   
6                          GradientBoostingClassifier        0.834100   
7                                       XGBClassifier        0.833500   
8   <catboost.core.CatBoostClassifier object at 0x...        0.833200   
9                                      LGBMClassifier        0.834500   
10                               KNeighborsClassifier        0.850100   

    Precision train  Recall train  F1 train  ROC AUC train  Accuracy test  \
0          0.720800      0.161300  0.263600       0.735000       0.816600   
1          0.716300      0.244600  0.364700       0.780700       0.825200   
2          0.778200      0.244600  0.372200       0.799100       0.829400   
3          0.477000      0.275700  0.349400       0.690100       0.790900   
4          0.683800      0.197000  0.305800       0.713400       0.816900   
5          0.732500      0.245000  0.367200       0.772300       0.826300   
6          0.782700      0.247200  0.375700       0.796500       0.829200   
7          0.778900      0.244900  0.372600       0.795000       0.829500   
8          0.768700      0.249200  0.376400       0.791200       0.829200   
9          0.778700      0.252000  0.380800       0.798400       0.828200   
10         0.735700      0.402000  0.520000       0.869400       0.802500   

    Precision test  Recall test  F1 test  ROC AUC test  
0         0.713100     0.153700 0.252900      0.733700  
1         0.701600     0.233900 0.350800      0.773000  
2         0.756200     0.228800 0.351300      0.782100  
3         0.469200     0.270600 0.343200      0.688100  
4         0.668300     0.185300 0.290200      0.711800  
5         0.717200     0.231000 0.349500      0.768900  
6         0.752400     0.229700 0.351900      0.783000  
7         0.757500     0.229100 0.351800      0.783000  
8         0.747000     0.233300 0.355500      0.783300  
9         0.741700     0.229400 0.350400      0.782500  
10        0.521400     0.267800 0.353800      0.688300

In [34]:
from imblearn.over_sampling import SMOTE
from collections import Counter

counter = Counter(y_train)
print('Before', counter)

smt = SMOTE(random_state=10)
X_train_sm, y_train_sm = smt.fit_resample(X_train, y_train)

counter = Counter(y_train_sm)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({0: 61743, 1: 61743})


In [35]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression())
])

In [36]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [37]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [38]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [39]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [40]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [41]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [42]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [43]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [44]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [45]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [46]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_sm, y_train_sm)

0:	learn: 0.6678755	total: 12.1ms	remaining: 1.98s
1:	learn: 0.6470580	total: 17.6ms	remaining: 1.44s
2:	learn: 0.6290947	total: 22.7ms	remaining: 1.23s
3:	learn: 0.6145969	total: 27.8ms	remaining: 1.12s
4:	learn: 0.6020108	total: 32.6ms	remaining: 1.04s
5:	learn: 0.5911371	total: 37.4ms	remaining: 992ms
6:	learn: 0.5826288	total: 42.3ms	remaining: 954ms
7:	learn: 0.5738909	total: 47.3ms	remaining: 928ms
8:	learn: 0.5667105	total: 52.2ms	remaining: 905ms
9:	learn: 0.5608196	total: 57.2ms	remaining: 886ms
10:	learn: 0.5557489	total: 62ms	remaining: 868ms
11:	learn: 0.5515710	total: 66.7ms	remaining: 850ms
12:	learn: 0.5464690	total: 71.8ms	remaining: 840ms
13:	learn: 0.5420795	total: 76.9ms	remaining: 829ms
14:	learn: 0.5390392	total: 81.6ms	remaining: 816ms
15:	learn: 0.5357667	total: 86.7ms	remaining: 808ms
16:	learn: 0.5323085	total: 92.1ms	remaining: 802ms
17:	learn: 0.5286501	total: 97.3ms	remaining: 795ms
18:	learn: 0.5257158	total: 103ms	remaining: 791ms
19:	learn: 0.5236374	tota

In [47]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " SMOTE")
    
    model_scores['Accuracy train'].append(model.score(X_train_sm, y_train_sm))
    pred_tr = model.predict(X_train_sm)
    prob_tr = model.predict_proba(X_train_sm)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_sm, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_sm, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_sm, pred_tr))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_sm, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    # model_scores['CV-5-Mean'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    # model_scores['CV-5-SD'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

In [48]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.818000   
1                              DecisionTreeClassifier        0.827900   
2                              RandomForestClassifier        0.833400   
3                                          GaussianNB        0.792700   
4                                         BernoulliNB        0.819400   
5                                  AdaBoostClassifier        0.829500   
6                          GradientBoostingClassifier        0.834100   
7                                       XGBClassifier        0.833500   
8   <catboost.core.CatBoostClassifier object at 0x...        0.833200   
9                                      LGBMClassifier        0.834500   
10                               KNeighborsClassifier        0.850100   
11                           LogisticRegression SMOTE        0.672500   
12                       DecisionTreeClassifier SMOTE        0.725100   
13                       RandomForestClassifier SMOTE        0.748800   
14                                   GaussianNB SMOTE        0.644300   
15                                  BernoulliNB SMOTE        0.665300   
16                           AdaBoostClassifier SMOTE        0.743200   
17                   GradientBoostingClassifier SMOTE        0.792000   
18                                XGBClassifier SMOTE        0.823000   
19  <catboost.core.CatBoostClassifier object at 0x...        0.816900   
20                               LGBMClassifier SMOTE        0.825000   
21                         KNeighborsClassifier SMOTE        0.846000   

    Precision train  Recall train  F1 train  ROC AUC train  Accuracy test  \
0          0.720800      0.161300  0.263600       0.735000       0.816600   
1          0.716300      0.244600  0.364700       0.780700       0.825200   
2          0.778200      0.244600  0.372200       0.799100       0.829400   
3          0.477000      0.275700  0.349400       0.690100       0.790900   
4          0.683800      0.197000  0.305800       0.713400       0.816900   
5          0.732500      0.245000  0.367200       0.772300       0.826300   
6          0.782700      0.247200  0.375700       0.796500       0.829200   
7          0.778900      0.244900  0.372600       0.795000       0.829500   
8          0.768700      0.249200  0.376400       0.791200       0.829200   
9          0.778700      0.252000  0.380800       0.798400       0.828200   
10         0.735700      0.402000  0.520000       0.869400       0.802500   
11         0.701800      0.599900  0.646900       0.736200       0.717500   
12         0.682700      0.840900  0.753600       0.806600       0.643900   
13         0.720800      0.812400  0.763800       0.841800       0.688800   
14         0.637700      0.668200  0.652600       0.685500       0.628700   
15         0.684700      0.612700  0.646700       0.714400       0.695400   
16         0.712500      0.815400  0.760500       0.831700       0.679800   
17         0.777800      0.817600  0.797200       0.876400       0.735500   
18         0.836900      0.802400  0.819300       0.902900       0.775700   
19         0.831900      0.794300  0.812600       0.896400       0.773900   
20         0.845400      0.795500  0.819700       0.905400       0.779800   
21         0.823200      0.881300  0.851300       0.931400       0.698900   

    Precision test  Recall test  F1 test  ROC AUC test  
0         0.713100     0.153700 0.252900      0.733700  
1         0.701600     0.233900 0.350800      0.773000  
2         0.756200     0.228800 0.351300      0.782100  
3         0.469200     0.270600 0.343200      0.688100  
4         0.668300     0.185300 0.290200      0.711800  
5         0.717200     0.231000 0.349500      0.768900  
6         0.752400     0.229700 0.351900      0.783000  
7         0.757500     0.229100 0.351800      0.783000  
8         0.747000     0.233300 0.355500      0.783300  
9         0.741700   

In [49]:
from imblearn.over_sampling import ADASYN
from collections import Counter

counter = Counter(y_train)
print('Before', counter)

ada = ADASYN(random_state=10)
X_train_as, y_train_as = ada.fit_resample(X_train, y_train)

counter = Counter(y_train_as)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({1: 65059, 0: 61743})


In [50]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression())
])

In [51]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [52]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [53]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [54]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [55]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [56]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [57]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [58]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [59]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [60]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [61]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_as, y_train_as)

0:	learn: 0.6716155	total: 6.71ms	remaining: 1.1s
1:	learn: 0.6523827	total: 12.8ms	remaining: 1.05s
2:	learn: 0.6370233	total: 18.4ms	remaining: 992ms
3:	learn: 0.6244954	total: 24ms	remaining: 966ms
4:	learn: 0.6138926	total: 29.2ms	remaining: 934ms
5:	learn: 0.6050510	total: 34.1ms	remaining: 905ms
6:	learn: 0.5969424	total: 39.3ms	remaining: 888ms
7:	learn: 0.5906843	total: 44.5ms	remaining: 874ms
8:	learn: 0.5838426	total: 49.6ms	remaining: 860ms
9:	learn: 0.5786681	total: 55ms	remaining: 852ms
10:	learn: 0.5742837	total: 60.2ms	remaining: 843ms
11:	learn: 0.5706918	total: 65.2ms	remaining: 831ms
12:	learn: 0.5673459	total: 70.9ms	remaining: 829ms
13:	learn: 0.5633065	total: 76.2ms	remaining: 822ms
14:	learn: 0.5610151	total: 81.2ms	remaining: 812ms
15:	learn: 0.5581144	total: 86.5ms	remaining: 806ms
16:	learn: 0.5560511	total: 91.7ms	remaining: 798ms
17:	learn: 0.5536332	total: 97ms	remaining: 792ms
18:	learn: 0.5494150	total: 103ms	remaining: 788ms
19:	learn: 0.5479422	total: 10

In [62]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " ADASYN")
    
    model_scores['Accuracy train'].append(model.score(X_train_as, y_train_as))
    pred_tr = model.predict(X_train_as)
    prob_tr = model.predict_proba(X_train_as)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_as, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_as, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_as, pred_tr))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_as, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    # model_scores['CV-5-Mean'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    # model_scores['CV-5-SD'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

In [63]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.818000   
1                              DecisionTreeClassifier        0.827900   
2                              RandomForestClassifier        0.833400   
3                                          GaussianNB        0.792700   
4                                         BernoulliNB        0.819400   
5                                  AdaBoostClassifier        0.829500   
6                          GradientBoostingClassifier        0.834100   
7                                       XGBClassifier        0.833500   
8   <catboost.core.CatBoostClassifier object at 0x...        0.833200   
9                                      LGBMClassifier        0.834500   
10                               KNeighborsClassifier        0.850100   
11                           LogisticRegression SMOTE        0.672500   
12                       DecisionTreeClassifier SMOTE        0.725100   
13                       RandomForestClassifier SMOTE        0.748800   
14                                   GaussianNB SMOTE        0.644300   
15                                  BernoulliNB SMOTE        0.665300   
16                           AdaBoostClassifier SMOTE        0.743200   
17                   GradientBoostingClassifier SMOTE        0.792000   
18                                XGBClassifier SMOTE        0.823000   
19  <catboost.core.CatBoostClassifier object at 0x...        0.816900   
20                               LGBMClassifier SMOTE        0.825000   
21                         KNeighborsClassifier SMOTE        0.846000   
22                          LogisticRegression ADASYN        0.646100   
23                      DecisionTreeClassifier ADASYN        0.715000   
24                      RandomForestClassifier ADASYN        0.732800   
25                                  GaussianNB ADASYN        0.571700   
26                                 BernoulliNB ADASYN        0.646300   
27                          AdaBoostClassifier ADASYN        0.731500   
28                  GradientBoostingClassifier ADASYN        0.776700   
29                               XGBClassifier ADASYN        0.816000   
30  <catboost.core.CatBoostClassifier object at 0x...        0.802600   
31                              LGBMClassifier ADASYN        0.818100   
32                        KNeighborsClassifier ADASYN        0.834700   

    Precision train  Recall train  F1 train  ROC AUC train  Accuracy test  \
0          0.720800      0.161300  0.263600       0.735000       0.816600   
1          0.716300      0.244600  0.364700       0.780700       0.825200   
2          0.778200      0.244600  0.372200       0.799100       0.829400   
3          0.477000      0.275700  0.349400       0.690100       0.790900   
4          0.683800      0.197000  0.305800       0.713400       0.816900   
5          0.732500      0.245000  0.367200       0.772300       0.826300   
6          0.782700      0.247200  0.375700       0.796500       0.829200   
7          0.778900      0.244900  0.372600       0.795000       0.829500   
8          0.768700      0.249200  0.376400       0.791200       0.829200   
9          0.778700      0.252000  0.380800       0.798400       0.828200   
10         0.735700      0.402000  0.520000       0.869400       0.802500   
11         0.701800      0.599900  0.646900       0.736200       0.717500   
12         0.682700      0.840900  0.753600       0.806600       0.643900   
13         0.720800      0.812400  0.763800       0.841800       0.688800   
14         0.637700      0.668200  0.652600       0.685500       0.628700   
15         0.684700      0.612700  0.646700       0.714400       0.695400   
16         0.712500      0.815400  0.760500       0.831700       0.679800   
17         0.777800      0.817600  0.797200       0.876400       0.735500   
18         0.836900      0.802400  0.819300       0.902900       0.775700   
19         0.831900 

In [64]:
from imblearn.combine import SMOTEENN
from collections import Counter

counter = Counter(y_train)
print('Before', counter)

enn = SMOTEENN(random_state=10)
X_train_enn, y_train_enn = enn.fit_resample(X_train, y_train)

counter = Counter(y_train_enn)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({1: 36139, 0: 34964})


In [65]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression())
])

In [66]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [67]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [68]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [69]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [70]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [71]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [72]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [73]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [74]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [75]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [76]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_enn, y_train_enn)

0:	learn: 0.6412028	total: 23.8ms	remaining: 3.91s
1:	learn: 0.5984213	total: 27.9ms	remaining: 2.27s
2:	learn: 0.5627716	total: 31.7ms	remaining: 1.71s
3:	learn: 0.5324754	total: 35.6ms	remaining: 1.43s
4:	learn: 0.5070728	total: 39.4ms	remaining: 1.26s
5:	learn: 0.4846151	total: 43.2ms	remaining: 1.14s
6:	learn: 0.4651743	total: 47ms	remaining: 1.06s
7:	learn: 0.4483423	total: 50.8ms	remaining: 998ms
8:	learn: 0.4339124	total: 54.5ms	remaining: 944ms
9:	learn: 0.4212246	total: 58.1ms	remaining: 901ms
10:	learn: 0.4104398	total: 61.6ms	remaining: 862ms
11:	learn: 0.4005207	total: 65.2ms	remaining: 832ms
12:	learn: 0.3919724	total: 68.8ms	remaining: 805ms
13:	learn: 0.3839688	total: 72.5ms	remaining: 782ms
14:	learn: 0.3771162	total: 76ms	remaining: 760ms
15:	learn: 0.3713063	total: 79.7ms	remaining: 743ms
16:	learn: 0.3652661	total: 83.5ms	remaining: 727ms
17:	learn: 0.3602911	total: 87.4ms	remaining: 714ms
18:	learn: 0.3553385	total: 91ms	remaining: 699ms
19:	learn: 0.3510630	total: 

In [77]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " ENN")
    
    model_scores['Accuracy train'].append(model.score(X_train_enn, y_train_enn))
    pred_tr = model.predict(X_train_enn)
    prob_tr = model.predict_proba(X_train_enn)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_enn, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_enn, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_enn, pred_tr))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_enn, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    # model_scores['CV-5-Mean'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    # model_scores['CV-5-SD'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

In [78]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.818000   
1                              DecisionTreeClassifier        0.827900   
2                              RandomForestClassifier        0.833400   
3                                          GaussianNB        0.792700   
4                                         BernoulliNB        0.819400   
5                                  AdaBoostClassifier        0.829500   
6                          GradientBoostingClassifier        0.834100   
7                                       XGBClassifier        0.833500   
8   <catboost.core.CatBoostClassifier object at 0x...        0.833200   
9                                      LGBMClassifier        0.834500   
10                               KNeighborsClassifier        0.850100   
11                           LogisticRegression SMOTE        0.672500   
12                       DecisionTreeClassifier SMOTE        0.725100   
13                       RandomForestClassifier SMOTE        0.748800   
14                                   GaussianNB SMOTE        0.644300   
15                                  BernoulliNB SMOTE        0.665300   
16                           AdaBoostClassifier SMOTE        0.743200   
17                   GradientBoostingClassifier SMOTE        0.792000   
18                                XGBClassifier SMOTE        0.823000   
19  <catboost.core.CatBoostClassifier object at 0x...        0.816900   
20                               LGBMClassifier SMOTE        0.825000   
21                         KNeighborsClassifier SMOTE        0.846000   
22                          LogisticRegression ADASYN        0.646100   
23                      DecisionTreeClassifier ADASYN        0.715000   
24                      RandomForestClassifier ADASYN        0.732800   
25                                  GaussianNB ADASYN        0.571700   
26                                 BernoulliNB ADASYN        0.646300   
27                          AdaBoostClassifier ADASYN        0.731500   
28                  GradientBoostingClassifier ADASYN        0.776700   
29                               XGBClassifier ADASYN        0.816000   
30  <catboost.core.CatBoostClassifier object at 0x...        0.802600   
31                              LGBMClassifier ADASYN        0.818100   
32                        KNeighborsClassifier ADASYN        0.834700   
33                             LogisticRegression ENN        0.796500   
34                         DecisionTreeClassifier ENN        0.847400   
35                         RandomForestClassifier ENN        0.871300   
36                                     GaussianNB ENN        0.756300   
37                                    BernoulliNB ENN        0.780100   
38                             AdaBoostClassifier ENN        0.855400   
39                     GradientBoostingClassifier ENN        0.891700   
40                                  XGBClassifier ENN        0.909900   
41  <catboost.core.CatBoostClassifier object at 0x...        0.894700   
42                                 LGBMClassifier ENN        0.909500   
43                           KNeighborsClassifier ENN        0.975300   

    Precision train  Recall train  F1 train  ROC AUC train  Accuracy test  \
0          0.720800      0.161300  0.263600       0.735000       0.816600   
1          0.716300      0.244600  0.364700       0.780700       0.825200   
2          0.778200      0.244600  0.372200       0.799100       0.829400   
3          0.477000      0.275700  0.349400       0.690100       0.790900   
4          0.683800      0.197000  0.305800       0.713400       0.816900   
5          0.732500      0.245000  0.367200       0.772300       0.826300   
6          0.782700      0.247200  0.375700       0.796500       0.829200   
7          0.778900      0.244900  0.372600       0.795000       0.829500   
8          0.768700      0.249200  0.376400       0.791200      

In [79]:
from imblearn.combine import SMOTEENN
from collections import Counter
from imblearn.under_sampling import EditedNearestNeighbours

counter = Counter(y_train)
print('Before', counter)

smote = SMOTE(random_state=10)
enn = EditedNearestNeighbours()

se = SMOTEENN(random_state=10, smote=smote, enn=enn)
X_train_se, y_train_se = se.fit_resample(X_train, y_train)

counter = Counter(y_train_se)
print('After', counter)

Before Counter({0: 61743, 1: 15623})
After Counter({0: 61743, 1: 36139})


In [80]:
lr_pipeline = Pipeline([
    ('lr_model', LogisticRegression())
])

In [81]:
dt_pipeline = Pipeline([
    ('dt_model', DecisionTreeClassifier(**rsearch_dt.best_params_,random_state=42))
])

In [82]:
rf_pipeline = Pipeline([
    ('rf_model', RandomForestClassifier(**rsearch_rf.best_params_,random_state=42))
])

In [83]:
gnb_pipeline = Pipeline([
    ('gnb_model', GaussianNB())
])

In [84]:
bnb_pipeline = Pipeline([
    ('bnb_model', BernoulliNB())
])

In [85]:
knn_pipeline = Pipeline([
    ('knn_model', KNeighborsClassifier())
])

In [86]:
ada_pipeline = Pipeline([
    ('rf_model', AdaBoostClassifier(**rsearch_ada.best_params_, random_state = 42))
])

In [87]:
gb_pipeline = Pipeline([
    ('rf_model', GradientBoostingClassifier(**rsearch_gb.best_params_, random_state = 42))
])

In [88]:
cb_pipeline = Pipeline([
    ('cb_model', CatBoostClassifier(**rsearch_cb.best_params_, random_state = 42))
])

In [89]:
lgbm_pipeline = Pipeline([
    ('lgbm_model', LGBMClassifier(**rsearch_lgbm.best_params_, random_state = 42))
])

In [90]:
xgb_pipeline = Pipeline([
    ('rf_model', XGBClassifier(**rsearch_xgb.best_params_, random_state = 42))
])

In [91]:
pipe_all = [lr_pipeline, dt_pipeline, rf_pipeline, gnb_pipeline, bnb_pipeline, ada_pipeline, gb_pipeline, xgb_pipeline, cb_pipeline, lgbm_pipeline,
            knn_pipeline]
            
for pipe in pipe_all:
  pipe.fit(X_train_se, y_train_se)

0:	learn: 0.6538305	total: 35ms	remaining: 5.74s
1:	learn: 0.6219031	total: 40.4ms	remaining: 3.29s
2:	learn: 0.5953704	total: 45.6ms	remaining: 2.46s
3:	learn: 0.5726377	total: 50.7ms	remaining: 2.04s
4:	learn: 0.5529330	total: 56.3ms	remaining: 1.8s
5:	learn: 0.5365647	total: 61.1ms	remaining: 1.62s
6:	learn: 0.5223545	total: 66.6ms	remaining: 1.5s
7:	learn: 0.5098682	total: 72.1ms	remaining: 1.42s
8:	learn: 0.4992561	total: 77.4ms	remaining: 1.34s
9:	learn: 0.4895697	total: 83ms	remaining: 1.28s
10:	learn: 0.4810706	total: 87.6ms	remaining: 1.23s
11:	learn: 0.4726967	total: 92.8ms	remaining: 1.18s
12:	learn: 0.4663603	total: 98.1ms	remaining: 1.15s
13:	learn: 0.4601501	total: 103ms	remaining: 1.11s
14:	learn: 0.4547053	total: 109ms	remaining: 1.08s
15:	learn: 0.4494760	total: 114ms	remaining: 1.06s
16:	learn: 0.4450476	total: 118ms	remaining: 1.03s
17:	learn: 0.4399459	total: 124ms	remaining: 1.01s
18:	learn: 0.4367149	total: 129ms	remaining: 995ms
19:	learn: 0.4333043	total: 135ms	

In [92]:
for model in pipe_all:
    
    model_scores['Model Name'].append(str(model[0]).split('(')[0] + " SMOTE + ENN")
    
    model_scores['Accuracy train'].append(model.score(X_train_se, y_train_se))
    pred_tr = model.predict(X_train_se)
    prob_tr = model.predict_proba(X_train_se)[:,1]
    model_scores['Precision train'].append(precision_score(y_train_se, pred_tr))
    model_scores['Recall train'].append(recall_score(y_train_se, pred_tr))
    model_scores['F1 train'].append(f1_score(y_train_se, pred_tr))
    model_scores['ROC AUC train'].append(roc_auc_score(y_train_se, prob_tr))
    
    model_scores['Accuracy test'].append(model.score(X_test, y_test))
    pred_ts = model.predict(X_test)
    prob_ts = model.predict_proba(X_test)[:,1]
    model_scores['Precision test'].append(precision_score(y_test, pred_ts))
    model_scores['Recall test'].append(recall_score(y_test, pred_ts))
    model_scores['F1 test'].append(f1_score(y_test, pred_ts))
    model_scores['ROC AUC test'].append(roc_auc_score(y_test, prob_ts))

    # model_scores['CV-5-Mean'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').mean())
    # model_scores['CV-5-SD'].append(cross_val_score(model,X,y,cv=KFold(n_splits=5,shuffle=True,random_state=10),scoring='f1_weighted').std())

In [93]:
pd.DataFrame(model_scores).round(4)

Model Name  Accuracy train  \
0                                  LogisticRegression        0.818000   
1                              DecisionTreeClassifier        0.827900   
2                              RandomForestClassifier        0.833400   
3                                          GaussianNB        0.792700   
4                                         BernoulliNB        0.819400   
5                                  AdaBoostClassifier        0.829500   
6                          GradientBoostingClassifier        0.834100   
7                                       XGBClassifier        0.833500   
8   <catboost.core.CatBoostClassifier object at 0x...        0.833200   
9                                      LGBMClassifier        0.834500   
10                               KNeighborsClassifier        0.850100   
11                           LogisticRegression SMOTE        0.672500   
12                       DecisionTreeClassifier SMOTE        0.725100   
13                       RandomForestClassifier SMOTE        0.748800   
14                                   GaussianNB SMOTE        0.644300   
15                                  BernoulliNB SMOTE        0.665300   
16                           AdaBoostClassifier SMOTE        0.743200   
17                   GradientBoostingClassifier SMOTE        0.792000   
18                                XGBClassifier SMOTE        0.823000   
19  <catboost.core.CatBoostClassifier object at 0x...        0.816900   
20                               LGBMClassifier SMOTE        0.825000   
21                         KNeighborsClassifier SMOTE        0.846000   
22                          LogisticRegression ADASYN        0.646100   
23                      DecisionTreeClassifier ADASYN        0.715000   
24                      RandomForestClassifier ADASYN        0.732800   
25                                  GaussianNB ADASYN        0.571700   
26                                 BernoulliNB ADASYN        0.646300   
27                          AdaBoostClassifier ADASYN        0.731500   
28                  GradientBoostingClassifier ADASYN        0.776700   
29                               XGBClassifier ADASYN        0.816000   
30  <catboost.core.CatBoostClassifier object at 0x...        0.802600   
31                              LGBMClassifier ADASYN        0.818100   
32                        KNeighborsClassifier ADASYN        0.834700   
33                             LogisticRegression ENN        0.796500   
34                         DecisionTreeClassifier ENN        0.847400   
35                         RandomForestClassifier ENN        0.871300   
36                                     GaussianNB ENN        0.756300   
37                                    BernoulliNB ENN        0.780100   
38                             AdaBoostClassifier ENN        0.855400   
39                     GradientBoostingClassifier ENN        0.891700   
40                                  XGBClassifier ENN        0.909900   
41  <catboost.core.CatBoostClassifier object at 0x...        0.894700   
42                                 LGBMClassifier ENN        0.909500   
43                           KNeighborsClassifier ENN        0.975300   
44                     LogisticRegression SMOTE + ENN        0.752400   
45                 DecisionTreeClassifier SMOTE + ENN        0.790200   
46                 RandomForestClassifier SMOTE + ENN        0.812900   
47                             GaussianNB SMOTE + ENN        0.712600   
48                            BernoulliNB SMOTE + ENN        0.739700   
49                     AdaBoostClassifier SMOTE + ENN        0.804400   
50             GradientBoostingClassifier SMOTE + ENN        0.845700   
51                          XGBClassifier SMOTE + ENN        0.885100   
52  <catboost.core.CatBoostClassifier object at 0x...        0.869400   
53                         LGBMClassifier SMOTE + ENN        0.884300   
54                   KNeighb

In [94]:
pd.DataFrame(model_scores).round(4).to_csv('tuned_models.csv', index = False)